In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs
import numpy as np

In [3]:

# Define a channel mapper or load one from file.
channel_mapper_exists = False

if channel_mapper_exists:
    mapper = qcs.load("<path/to/channel_mapper.qcs>")
else:
    # generate an empty channel mapper with the correct address
    mapper = qcs.ChannelMapper("127.0.0.1")

readout_pulse_channels = qcs.Channels([0, 1], "readout_pulse", absolute_phase=True)
readout_acquisition_channels = qcs.Channels(
    [0, 1], "readout_acquisition", absolute_phase=True
)

In [4]:
# Define a program to run
program = qcs.Program()
frequency = qcs.Scalar("frequency", dtype=float)
waveform = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(), 1, frequency)
int_filter = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(), 1, [5.1e9, 5.15e9])
program.add_waveform(waveform, readout_pulse_channels)
program.add_acquisition(int_filter, readout_acquisition_channels)
program.n_shots(50)
frequencies = qcs.Array("frequencies", value=np.linspace(5e9, 5.25e9, 50))
program.sweep(frequencies, frequency)
program.draw()

In [5]:
# Setup live plotting to display the two digitizer channels
backend = qcs.HclBackend(
    channel_mapper=mapper,
    fpga_postprocessing=True,
    live_plotting_config=readout_acquisition_channels,
)

In [6]:
# Set this to True if connected to hardware
run_on_hw = False

if run_on_hw:
    # Execute the program.
    # While running, live IQ data for the frequency sweep will be shown.
    program_result = qcs.Executor(backend).execute(program)

    # Plot the "static" version of the plot to compare the results
    program_result.plot_iq(channel_subplots=False, plot_type="linear")

In [7]:
qubits = qcs.Qudits([0, 1])
calibration_set = qcs.experiments.make_calibration_set(qubits=len(qubits))

In [8]:
# Create a resonator spectroscopy experiment with live plotting
# Note that the channels for live plotting match the channels from the calibration set.
backend = qcs.HclBackend(
    channel_mapper=mapper,
    fpga_postprocessing=True,
    live_plotting_config=readout_acquisition_channels,
)

res_spectroscopy2D = qcs.experiments.ResonatorSpectroscopy2D(
    backend=backend,
    calibration_set=calibration_set,
    qubits=qubits,
    operation="measurement",
)

In [9]:
# Draw the program to view the operations to be performed on hardware
res_spectroscopy2D.draw()

In [10]:
# Retrieve the readout frequencies stored in the calibration set for the target qubits
current_freq = res_spectroscopy2D.calibration_set.variables.readout_frequencies[
    [0, 1]
].value

# Set the range for sweeping the readout pulse frequency
start_frequency = current_freq - 200e6
end_frequency = current_freq + 200e6
freq_steps = 9
freq_scan_values = np.linspace(start_frequency, end_frequency, freq_steps)

In [11]:
# Set the range for sweeping the readout pulse amplitude (units = V)
start_amplitude = 0.1 if len(qubits) == 1 else [0.1] * len(qubits)
end_amplitude = 1 if len(qubits) == 1 else [1] * len(qubits)
ampl_steps = 10
ampl_scan_values = np.linspace(start_amplitude, end_amplitude, ampl_steps)

In [12]:
# Configure the repetitions for this experiment
res_spectroscopy2D.configure_repetitions(
    frequencies=freq_scan_values,
    frequency_name="readout_frequencies",
    amplitudes=ampl_scan_values,
    amplitude_name="readout_pulse_amplitudes",
    n_shots=10,
)

In [13]:
if run_on_hw:
    res_spectroscopy2D.execute()